In [1]:
# 禁用 wandb 功能（必须在 import wandb 前设置）
import os
os.environ["WANDB_DISABLED"] = "true"
os.environ["WANDB_MODE"] = "disabled"
os.environ["WANDB_START_METHOD"] = "thread"

# 然后再导入
import wandb
# 不要调用 wandb.init()，除非你真的要上传实验日志

In [2]:
from pathlib import Path
import torch
from PIL import Image
from ray.rllib.models.torch.torch_distributions import TorchDiagGaussian
from ray.tune.result import TRAINING_ITERATION
from ray.rllib.algorithms.callbacks import DefaultCallbacks
from ray.rllib.core import (
    COMPONENT_LEARNER,
    COMPONENT_LEARNER_GROUP,
    COMPONENT_RL_MODULE,
)
from ray.rllib.core.rl_module.default_model_config import DefaultModelConfig
from ray.rllib.examples.envs.classes.multi_agent import MultiAgentPendulum
from ray.rllib.utils.metrics import (
    ENV_RUNNER_RESULTS,
    EPISODE_RETURN_MEAN,
    NUM_ENV_STEPS_SAMPLED_LIFETIME,
)
from ray.rllib.utils.numpy import convert_to_numpy
from ray.rllib.utils.test_utils import (
    add_rllib_example_script_args,
    check,
    # run_rllib_example_script_experiment,
)
from ray.tune.registry import get_trainable_cls, register_env


/home/qrbao/anaconda3/envs/rllib/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
2025-07-17 16:38:11,864	INFO util.py:154 -- Missing packages: ['ipywidgets']. Run `pip install -U ipywidgets`, then restart the notebook server for rich notebook output.
2025-07-17 16:38:12,121	INFO util.py:154 -- Missing packages: ['ipywidgets']. Run `pip install -U ipywidgets`, then restart the notebook server for rich notebook output.


In [3]:

from pettingzoo.sisl import waterworld_v4

from ray.rllib.core.rl_module.default_model_config import DefaultModelConfig
from ray.rllib.core.rl_module.multi_rl_module import MultiRLModuleSpec
from ray.rllib.core.rl_module.rl_module import RLModuleSpec
from ray.rllib.env.wrappers.pettingzoo_env import PettingZooEnv
# from ray.rllib.utils.test_utils import (
#     # add_rllib_example_script_args,
#     run_rllib_example_script_experiment,
# )
from ray.tune.registry import get_trainable_cls, register_env
import os

import gymnasium as gym
import numpy as np
import tree  # pip install dm_tree

from ray.rllib.core import DEFAULT_MODULE_ID
from ray.rllib.core.columns import Columns
from ray.rllib.core.rl_module.rl_module import RLModule
from ray.rllib.utils.framework import try_import_torch
from ray.rllib.utils.numpy import convert_to_numpy, softmax
from ray.rllib.utils.metrics import (
    ENV_RUNNER_RESULTS,
    EPISODE_RETURN_MEAN,
)

torch, _ = try_import_torch()

import wandb

In [4]:
import argparse
import json
import logging
import os
import pprint
import random
import re
import time
from typing import (
    TYPE_CHECKING,
    Any,
    Dict,
    List,
    Optional,
    Tuple,
    Type,
    Union,
)

import gymnasium as gym
from gymnasium.spaces import Box, Discrete, MultiDiscrete, MultiBinary
from gymnasium.spaces import Dict as GymDict
from gymnasium.spaces import Tuple as GymTuple
import numpy as np
import tree  # pip install dm_tree

import ray
from ray import tune
from ray.air.integrations.wandb import WandbLoggerCallback, WANDB_ENV_VAR
from ray.rllib.core import DEFAULT_MODULE_ID, Columns
from ray.rllib.env.wrappers.atari_wrappers import is_atari, wrap_deepmind
from ray.rllib.utils.annotations import OldAPIStack
from ray.rllib.utils.framework import try_import_jax, try_import_tf, try_import_torch
from ray.rllib.utils.metrics import (
    DIFF_NUM_GRAD_UPDATES_VS_SAMPLER_POLICY,
    ENV_RUNNER_RESULTS,
    EPISODE_RETURN_MEAN,
    EVALUATION_RESULTS,
    NUM_ENV_STEPS_TRAINED,
    NUM_ENV_STEPS_SAMPLED_LIFETIME,
)
from ray.rllib.utils.typing import ResultDict
from ray.rllib.utils.error import UnsupportedSpaceException
from ray.tune import CLIReporter
from ray.tune.result import TRAINING_ITERATION

if TYPE_CHECKING:
    from ray.rllib.algorithms import Algorithm, AlgorithmConfig
    from ray.rllib.offline.dataset_reader import DatasetReader

jax, _ = try_import_jax()
tf1, tf, tfv = try_import_tf()
torch, _ = try_import_torch()

logger = logging.getLogger(__name__)

In [6]:

class WandbLoggingCallback(DefaultCallbacks):
    def on_train_result(self, *, algorithm, result, **kwargs):
        # 记录训练过程中的健康值
        print("[DEBUG] on_train_result 被调用")
        mean_reward = result.get("episode_reward_mean") or result.get("hist_stats", {}).get("episode_reward_mean")

        if mean_reward is not None:
            # Log 到 wandb
            wandb.log({"episode_reward_mean": mean_reward, "training_iteration": result.get("training_iteration", 0)})
        
        # 新增：记录健康值（如果可以从算法中获取）
        # 注意：这里可能需要根据实际情况调整获取健康值的方式
        try:
            # 尝试从环境中获取健康值数据
            env_runner_results = result.get("env_runners", {})
            if env_runner_results:
                # 这里需要根据RLLib的具体结构来获取健康值
                # 可能需要通过自定义metrics来实现
                pass
        except Exception as e:
            print(f"获取健康值时出错: {e}")



In [7]:

# 设置参数
import sys
sys.argv = [
    'notebook_script.py',
    # '--algo=SAC',  # 使用SAC算法
    '--enable-new-api-stack',
    '--num-agents=10',
    # 新增参数用于指定predator和prey的数量
    '--n-predators=5',
    '--wandb-key=fdd7656f474bba144dea1887bcdab534bc7df647',
    '--wandb-project=waterworld-v4',
    '--n-preys=5', 
    '--checkpoint-at-end',
    '--stop-reward=200.0',
    '--checkpoint-freq=1',
]

parser = add_rllib_example_script_args(
    default_iters=2,
    default_timesteps=10000,
    default_reward=0.0,
)

# parser.add_argument(
#     "--algo", type=str, default="SAC", help="The RLlib-registered algorithm to use."
# )
# 添加新的参数解析
parser.add_argument(
    "--n-predators",
    type=int,
    default=2,
    help="Number of predator agents"
)
parser.add_argument(
    "--n-preys", 
    type=int,
    default=2,
    help="Number of prey agents"
)
parser.add_argument(
    "--use-onnx-for-inference",
    action="store_true",
    help="Whether to convert the loaded module to ONNX format and then perform "
    "inference through this ONNX model.",
)
parser.add_argument(
    "--explore-during-inference",
    action="store_true",
    help="Whether the trained policy should use exploration during action "
    "inference.",
)
parser.add_argument(
    "--num-episodes-during-inference",
    type=int,
    default=10,
    help="Number of episodes to do inference over (after restoring from a checkpoint).",
)

agent_algos = ["PPO", "PPO", "DQN", "DQN", "A2C","PPO", "PPO", "DQN", "DQN", "A2C"]

args = parser.parse_args()

# 验证参数
assert args.n_predators > 0, "Must set --n-predators > 0 when running this script!"
assert args.n_preys > 0, "Must set --n-preys > 0 when running this script!"
assert (
    args.enable_new_api_stack
), "Must set --enable-new-api-stack when running this script!"

# 计算总智能体数量
total_agents = args.n_predators + args.n_preys
print(f"参数解析完成: n_predators={args.n_predators}, n_preys={args.n_preys}, total_agents={total_agents}, algo={args.algo}")

# 创建输出目录
output_dir = Path("outputs")
output_dir.mkdir(exist_ok=True)

参数解析完成: n_predators=5, n_preys=5, total_agents=10, algo=PPO


In [8]:
print(args)

Namespace(algo='PPO', enable_new_api_stack=True, framework='torch', env=None, num_env_runners=None, num_envs_per_env_runner=None, num_agents=10, evaluation_num_env_runners=0, evaluation_interval=0, evaluation_duration=10, evaluation_duration_unit='episodes', evaluation_parallel_to_training=False, output=None, log_level=None, no_tune=False, num_samples=1, max_concurrent_trials=None, verbose=2, checkpoint_freq=1, checkpoint_at_end=True, wandb_key='fdd7656f474bba144dea1887bcdab534bc7df647', wandb_project='waterworld-v4', wandb_run_name=None, stop_reward=200.0, stop_iters=2, stop_timesteps=10000, as_test=False, as_release_test=False, num_learners=None, num_cpus_per_learner=None, num_gpus_per_learner=None, num_aggregator_actors_per_learner=None, num_cpus=0, local_mode=False, num_gpus=None, n_predators=5, n_preys=5, use_onnx_for_inference=False, explore_during_inference=False, num_episodes_during_inference=10)


In [9]:
wandb.init(project=args.wandb_project, config=vars(args))

wandb: WARNING `start_method` is deprecated and will be removed in a future version of wandb. This setting is currently non-functional and safely ignored.


In [10]:
# 修改环境注册，传递predator和prey的数量
register_env("env", lambda _: PettingZooEnv(
    waterworld_v4.env(
        n_predators=args.n_predators,
        n_preys=args.n_preys,
        agent_algorithms=agent_algos,
        initial_health=100.0
    )
))

In [11]:

# 创建新的policies字典，匹配环境中的agent命名
predator_policies = [f"predator_{i}" for i in range(args.n_predators)]
prey_policies = [f"prey_{i}" for i in range(args.n_preys)]
all_policies = predator_policies + prey_policies
print(all_policies)

['predator_0', 'predator_1', 'predator_2', 'predator_3', 'predator_4', 'prey_0', 'prey_1', 'prey_2', 'prey_3', 'prey_4']


In [12]:

# 创建RL module specs字典
rl_module_specs = {p: RLModuleSpec() for p in all_policies}
print(f"创建的policies: {list(all_policies)}")
print(f"创建的RL module specs: {list(rl_module_specs.keys())}")


创建的policies: ['predator_0', 'predator_1', 'predator_2', 'predator_3', 'predator_4', 'prey_0', 'prey_1', 'prey_2', 'prey_3', 'prey_4']
创建的RL module specs: ['predator_0', 'predator_1', 'predator_2', 'predator_3', 'predator_4', 'prey_0', 'prey_1', 'prey_2', 'prey_3', 'prey_4']


In [13]:
base_config = (
    get_trainable_cls(args.algo)
    .get_default_config()
    .environment("env")
    .multi_agent(
        # 在新API中，只需要指定policy_mapping_fn
        policies=set(all_policies),
        policy_mapping_fn=(lambda aid, *args, **kwargs: aid),
    )
    .training(
        model={
            "vf_share_layers": True,
        },
        vf_loss_coeff=0.005,
    )
    .rl_module(
        rl_module_spec=MultiRLModuleSpec(
            rl_module_specs=rl_module_specs,
        ),
        model_config=DefaultModelConfig(vf_share_layers=True),
    )
    .callbacks(WandbLoggingCallback)
)


/home/qrbao/anaconda3/envs/rllib/lib/python3.10/site-packages/gymnasium/spaces/box.py:235: UserWarning: WARN: Box low's precision lowered by casting to float32, current low.dtype=float64
  gym.logger.warn(
/home/qrbao/anaconda3/envs/rllib/lib/python3.10/site-packages/gymnasium/spaces/box.py:305: UserWarning: WARN: Box high's precision lowered by casting to float32, current high.dtype=float64
  gym.logger.warn(
/home/qrbao/anaconda3/envs/rllib/lib/python3.10/site-packages/gymnasium/utils/passive_env_checker.py:134: UserWarning: WARN: The obs returned by the `reset()` method was expecting numpy array dtype to be float32, actual type: float64
  logger.warn(
/home/qrbao/anaconda3/envs/rllib/lib/python3.10/site-packages/gymnasium/utils/passive_env_checker.py:158: UserWarning: WARN: The obs returned by the `reset()` method is not within the observation space.
  logger.warn(f"{pre} is not within the observation space.")


In [14]:
# from ray.rllib.core.rl_module.multi_rl_module import MultiRLModuleSpec
# from ray.rllib.core.rl_module.default_model_config import DefaultModelConfig

# base_config = (
#     get_trainable_cls(args.algo)
#     .get_default_config()
#     .environment("env")
#     .multi_agent(
#         policies=set(all_policies),
#         policy_mapping_fn=(lambda aid, *args, **kwargs: aid),
#     )
#     .training(
#         gamma=0.9,
#         actor_lr=0.001,
#         critic_lr=0.002,
#         train_batch_size_per_learner=32,

#         # 👇 添加 replay_buffer_config 参数
#         replay_buffer_config={
#             "_enable_replay_buffer_api": True,
#             "type": "EpisodeReplayBuffer",  # or "MultiAgentPrioritizedReplayBuffer"
#             "capacity": 100000,
#             "replay_sequence_length": 1,
#         },
#     )
#     .rl_module(
#         rl_module_spec=MultiRLModuleSpec(
#             rl_module_specs=rl_module_specs,
#         ),
#         model_config=DefaultModelConfig(vf_share_layers=True),
#     )
#     .callbacks(WandbLoggingCallback)
# )

In [15]:
def add_rllib_example_script_args(
    parser: Optional[argparse.ArgumentParser] = None,
    default_reward: float = 100.0,
    default_iters: int = 200,
    default_timesteps: int = 100000,
) -> argparse.ArgumentParser:
    """Adds RLlib-typical (and common) examples scripts command line args to a parser.

    TODO (sven): This function should be used by most of our examples scripts, which
     already mostly have this logic in them (but written out).

    Args:
        parser: The parser to add the arguments to. If None, create a new one.
        default_reward: The default value for the --stop-reward option.
        default_iters: The default value for the --stop-iters option.
        default_timesteps: The default value for the --stop-timesteps option.

    Returns:
        The altered (or newly created) parser object.
    """
    if parser is None:
        parser = argparse.ArgumentParser()

    # Algo and Algo config options.
    parser.add_argument(
        "--algo", type=str, default="SAC", help="The RLlib-registered algorithm to use."
    )
    parser.add_argument(
        "--enable-new-api-stack",
        action="store_true",
        help="Whether to use the `enable_rl_module_and_learner` config setting.",
    )
    parser.add_argument(
        "--framework",
        choices=["tf", "tf2", "torch"],
        default="torch",
        help="The DL framework specifier.",
    )
    parser.add_argument(
        "--env",
        type=str,
        default=None,
        help="The gym.Env identifier to run the experiment with.",
    )
    parser.add_argument(
        "--num-env-runners",
        type=int,
        default=None,
        help="The number of (remote) EnvRunners to use for the experiment.",
    )
    parser.add_argument(
        "--num-envs-per-env-runner",
        type=int,
        default=None,
        help="The number of (vectorized) environments per EnvRunner. Note that "
        "this is identical to the batch size for (inference) action computations.",
    )
    parser.add_argument(
        "--num-agents",
        type=int,
        default=0,
        help="If 0 (default), will run as single-agent. If > 0, will run as "
        "multi-agent with the environment simply cloned n times and each agent acting "
        "independently at every single timestep. The overall reward for this "
        "experiment is then the sum over all individual agents' rewards.",
    )

    # Evaluation options.
    parser.add_argument(
        "--evaluation-num-env-runners",
        type=int,
        default=0,
        help="The number of evaluation (remote) EnvRunners to use for the experiment.",
    )
    parser.add_argument(
        "--evaluation-interval",
        type=int,
        default=0,
        help="Every how many iterations to run one round of evaluation. "
        "Use 0 (default) to disable evaluation.",
    )
    parser.add_argument(
        "--evaluation-duration",
        type=lambda v: v if v == "auto" else int(v),
        default=10,
        help="The number of evaluation units to run each evaluation round. "
        "Use `--evaluation-duration-unit` to count either in 'episodes' "
        "or 'timesteps'. If 'auto', will run as many as possible during train pass ("
        "`--evaluation-parallel-to-training` must be set then).",
    )
    parser.add_argument(
        "--evaluation-duration-unit",
        type=str,
        default="episodes",
        choices=["episodes", "timesteps"],
        help="The evaluation duration unit to count by. One of 'episodes' or "
        "'timesteps'. This unit will be run `--evaluation-duration` times in each "
        "evaluation round. If `--evaluation-duration=auto`, this setting does not "
        "matter.",
    )
    parser.add_argument(
        "--evaluation-parallel-to-training",
        action="store_true",
        help="Whether to run evaluation parallel to training. This might help speed up "
        "your overall iteration time. Be aware that when using this option, your "
        "reported evaluation results are referring to one iteration before the current "
        "one.",
    )

    # RLlib logging options.
    parser.add_argument(
        "--output",
        type=str,
        default=None,
        help="The output directory to write trajectories to, which are collected by "
        "the algo's EnvRunners.",
    )
    parser.add_argument(
        "--log-level",
        type=str,
        default=None,  # None -> use default
        choices=["INFO", "DEBUG", "WARN", "ERROR"],
        help="The log-level to be used by the RLlib logger.",
    )

    # tune.Tuner options.
    parser.add_argument(
        "--no-tune",
        action="store_true",
        help="Whether to NOT use tune.Tuner(), but rather a simple for-loop calling "
        "`algo.train()` repeatedly until one of the stop criteria is met.",
    )
    parser.add_argument(
        "--num-samples",
        type=int,
        default=1,
        help="How many (tune.Tuner.fit()) experiments to execute - if possible in "
        "parallel.",
    )
    parser.add_argument(
        "--max-concurrent-trials",
        type=int,
        default=None,
        help="How many (tune.Tuner) trials to run concurrently.",
    )
    parser.add_argument(
        "--verbose",
        type=int,
        default=2,
        help="The verbosity level for the `tune.Tuner()` running the experiment.",
    )
    parser.add_argument(
        "--checkpoint-freq",
        type=int,
        default=0,
        help=(
            "The frequency (in training iterations) with which to create checkpoints. "
            "Note that if --wandb-key is provided, all checkpoints will "
            "automatically be uploaded to WandB."
        ),
    )
    parser.add_argument(
        "--checkpoint-at-end",
        action="store_true",
        help=(
            "Whether to create a checkpoint at the very end of the experiment. "
            "Note that if --wandb-key is provided, all checkpoints will "
            "automatically be uploaded to WandB."
        ),
    )

    # WandB logging options.
    parser.add_argument(
        "--wandb-key",
        type=str,
        default=None,
        help="The WandB API key to use for uploading results.",
    )
    parser.add_argument(
        "--wandb-project",
        type=str,
        default=None,
        help="The WandB project name to use.",
    )
    parser.add_argument(
        "--wandb-run-name",
        type=str,
        default=None,
        help="The WandB run name to use.",
    )

    # Experiment stopping and testing criteria.
    parser.add_argument(
        "--stop-reward",
        type=float,
        default=default_reward,
        help="Reward at which the script should stop training.",
    )
    parser.add_argument(
        "--stop-iters",
        type=int,
        default=default_iters,
        help="The number of iterations to train.",
    )
    parser.add_argument(
        "--stop-timesteps",
        type=int,
        default=default_timesteps,
        help="The number of (environment sampling) timesteps to train.",
    )
    parser.add_argument(
        "--as-test",
        action="store_true",
        help="Whether this script should be run as a test. If set, --stop-reward must "
        "be achieved within --stop-timesteps AND --stop-iters, otherwise this "
        "script will throw an exception at the end.",
    )
    parser.add_argument(
        "--as-release-test",
        action="store_true",
        help="Whether this script should be run as a release test. If set, "
        "all that applies to the --as-test option is true, plus, a short JSON summary "
        "will be written into a results file whose location is given by the ENV "
        "variable `TEST_OUTPUT_JSON`.",
    )

    # Learner scaling options.
    parser.add_argument(
        "--num-learners",
        type=int,
        default=None,
        help="The number of Learners to use. If `None`, use the algorithm's default "
        "value.",
    )
    parser.add_argument(
        "--num-cpus-per-learner",
        type=float,
        default=None,
        help="The number of CPUs per Learner to use. If `None`, use the algorithm's "
        "default value.",
    )
    parser.add_argument(
        "--num-gpus-per-learner",
        type=float,
        default=None,
        help="The number of GPUs per Learner to use. If `None` and there are enough "
        "GPUs for all required Learners (--num-learners), use a value of 1, "
        "otherwise 0.",
    )
    parser.add_argument(
        "--num-aggregator-actors-per-learner",
        type=int,
        default=None,
        help="The number of Aggregator actors to use per Learner. If `None`, use the "
        "algorithm's default value.",
    )

    # Ray init options.
    parser.add_argument("--num-cpus", type=int, default=0)
    parser.add_argument(
        "--local-mode",
        action="store_true",
        help="Init Ray in local mode for easier debugging.",
    )

    # Old API stack: config.num_gpus.
    parser.add_argument(
        "--num-gpus",
        type=int,
        default=None,
        help="The number of GPUs to use (only on the old API stack).",
    )

    return parser

In [17]:
# TODO (sven): Make this the de-facto, well documented, and unified utility for most of
#  our tests:
#  - CI (label: "learning_tests")
#  - release tests (benchmarks)
#  - example scripts
def run_rllib_example_script_experiment(
    base_config: "AlgorithmConfig",
    args: Optional[argparse.Namespace] = None,
    *,
    stop: Optional[Dict] = None,
    success_metric: Optional[Dict] = None,
    trainable: Optional[Type] = None,
    tune_callbacks: Optional[List] = None,
    keep_config: bool = False,
    keep_ray_up: bool = False,
    scheduler=None,
    progress_reporter=None,
) -> Union[ResultDict, tune.result_grid.ResultGrid]:
    """Given an algorithm config and some command line args, runs an experiment.

    There are some constraints on what properties must be defined in `args`.
    It should ideally be generated via calling
    `args = add_rllib_example_script_args()`, which can be found in this very module
    here.

    The function sets up an Algorithm object from the given config (altered by the
    contents of `args`), then runs the Algorithm via Tune (or manually, if
    `args.no_tune` is set to True) using the stopping criteria in `stop`.

    At the end of the experiment, if `args.as_test` is True, checks, whether the
    Algorithm reached the `success_metric` (if None, use `env_runners/
    episode_return_mean` with a minimum value of `args.stop_reward`).

    See https://github.com/ray-project/ray/tree/master/rllib/examples for an overview
    of all supported command line options.

    Args:
        
        
        
        
        
        fig: The AlgorithmConfig object to use for this experiment. This base
            config will be automatically "extended" based on some of the provided
            `args`. For example, `args.num_env_runners` is used to set
            `config.num_env_runners`, etc..
        args: A argparse.Namespace object, ideally returned by calling
            `args = add_rllib_example_script_args()`. It must have the following
            properties defined: `stop_iters`, `stop_reward`, `stop_timesteps`,
            `no_tune`, `verbose`, `checkpoint_freq`, `as_test`. Optionally, for WandB
            logging: `wandb_key`, `wandb_project`, `wandb_run_name`.
        stop: An optional dict mapping ResultDict key strings (using "/" in case of
            nesting, e.g. "env_runners/episode_return_mean" for referring to
            `result_dict['env_runners']['episode_return_mean']` to minimum
            values, reaching of which will stop the experiment). Default is:
            {
            "env_runners/episode_return_mean": args.stop_reward,
            "training_iteration": args.stop_iters,
            "num_env_steps_sampled_lifetime": args.stop_timesteps,
            }
        success_metric: Only relevant if `args.as_test` is True.
            A dict mapping a single(!) ResultDict key string (using "/" in
            case of nesting, e.g. "env_runners/episode_return_mean" for referring
            to `result_dict['env_runners']['episode_return_mean']` to a single(!)
            minimum value to be reached in order for the experiment to count as
            successful. If `args.as_test` is True AND this `success_metric` is not
            reached with the bounds defined by `stop`, will raise an Exception.
        trainable: The Trainable sub-class to run in the tune.Tuner. If None (default),
            use the registered RLlib Algorithm class specified by args.algo.
        tune_callbacks: A list of Tune callbacks to configure with the tune.Tuner.
            In case `args.wandb_key` is provided, appends a WandB logger to this
            list.
        keep_config: Set this to True, if you don't want this utility to change the
            given `base_config` in any way and leave it as-is. This is helpful
            for those example scripts which demonstrate how to set config settings
            that are otherwise taken care of automatically in this function (e.g.
            `num_env_runners`).

    Returns:
        The last ResultDict from a --no-tune run OR the tune.Tuner.fit()
        results.
    """
    # if args is None:#(not use this one line)
    #     parser = add_rllib_example_script_args()
    #     args = parser.parse_args()

    # # If run --as-release-test, --as-test must also be set.
    # if args.as_release_test:
    #     args.as_test = True

    # Initialize Ray.
    ray.init(
        num_cpus=args.num_cpus or None,
        local_mode=args.local_mode,
        ignore_reinit_error=True,
    )

    # Define one or more stopping criteria.
    if stop is None:
        stop = {
            f"{ENV_RUNNER_RESULTS}/{EPISODE_RETURN_MEAN}": args.stop_reward,
            f"{ENV_RUNNER_RESULTS}/{NUM_ENV_STEPS_SAMPLED_LIFETIME}": (
                args.stop_timesteps
            ),
            TRAINING_ITERATION: args.stop_iters,
        }

    config = base_config

    # Enhance the `base_config`, based on provided `args`.
    if not keep_config:
        # Set the framework.
        config.framework(args.framework)

        # Add an env specifier (only if not already set in config)?(not use this one)
        if args.env is not None and config.env is None:
            config.environment(args.env)

        # # Disable the new API stack?(not use this one )
        # if not args.enable_new_api_stack:
        #     config.api_stack(
        #         enable_rl_module_and_learner=False,
        #         enable_env_runner_and_connector_v2=False,
        #     )

        # Define EnvRunner scaling and behavior.(no use this two)
        # if args.num_env_runners is not None:
        #     config.env_runners(num_env_runners=args.num_env_runners)
        # if args.num_envs_per_env_runner is not None:
        #     config.env_runners(num_envs_per_env_runner=args.num_envs_per_env_runner)

        # Define compute resources used automatically (only using the --num-learners
        # and --num-gpus-per-learner args).
        # New stack.
        if config.enable_rl_module_and_learner:
            # if args.num_gpus is not None and args.num_gpus > 0:
            #     raise ValueError(
            #         "--num-gpus is not supported on the new API stack! To train on "
            #         "GPUs, use the command line options `--num-gpus-per-learner=1` and "
            #         "`--num-learners=[your number of available GPUs]`, instead."
            #     )

            # Do we have GPUs available in the cluster?
            num_gpus_available = ray.cluster_resources().get("GPU", 0)
            # Number of actual Learner instances (including the local Learner if
            # `num_learners=0`).
            num_actual_learners = (
                args.num_learners
                if args.num_learners is not None
                else config.num_learners
            ) or 1  # 1: There is always a local Learner, if num_learners=0.
            # How many were hard-requested by the user
            # (through explicit `--num-gpus-per-learner >= 1`).
            num_gpus_requested = (args.num_gpus_per_learner or 0) * num_actual_learners
            # Number of GPUs needed, if `num_gpus_per_learner=None` (auto).
            num_gpus_needed_if_available = (
                args.num_gpus_per_learner
                if args.num_gpus_per_learner is not None
                else 1
            ) * num_actual_learners
            # Define compute resources used.
            # config.resources(num_gpus=0)  # old API stack setting
            # if args.num_learners is not None:
            #     config.learners(num_learners=args.num_learners)

            # # User wants to use aggregator actors per Learner.
            # if args.num_aggregator_actors_per_learner is not None:
            #     config.learners(
            #         num_aggregator_actors_per_learner=(
            #             args.num_aggregator_actors_per_learner
            #         )
            #     )

            # User wants to use GPUs if available, but doesn't hard-require them.
            if args.num_gpus_per_learner is None:
                if num_gpus_available >= num_gpus_needed_if_available:
                    config.learners(num_gpus_per_learner=1)
                else:
                    config.learners(num_gpus_per_learner=0)
            # User hard-requires n GPUs, but they are not available -> Error.
            elif num_gpus_available < num_gpus_requested:
                raise ValueError(
                    "You are running your script with --num-learners="
                    f"{args.num_learners} and --num-gpus-per-learner="
                    f"{args.num_gpus_per_learner}, but your cluster only has "
                    f"{num_gpus_available} GPUs!"
                )

            # All required GPUs are available -> Use them.
            else:
                config.learners(num_gpus_per_learner=args.num_gpus_per_learner)

            # Set CPUs per Learner.
            if args.num_cpus_per_learner is not None:
                config.learners(num_cpus_per_learner=args.num_cpus_per_learner)

        # Old stack (override only if arg was provided by user).
        elif args.num_gpus is not None:
            config.resources(num_gpus=args.num_gpus)

        # Evaluation setup.
        if args.evaluation_interval > 0:
            config.evaluation(
                evaluation_num_env_runners=args.evaluation_num_env_runners,
                evaluation_interval=args.evaluation_interval,
                evaluation_duration=args.evaluation_duration,
                evaluation_duration_unit=args.evaluation_duration_unit,
                evaluation_parallel_to_training=args.evaluation_parallel_to_training,
            )

        # Set the log-level (if applicable).(not use this one)
        if args.log_level is not None:
            config.debugging(log_level=args.log_level)

        # Set the output dir (if applicable)..(not use this one)
        if args.output is not None:
            config.offline_data(output=args.output)

    # Run the experiment w/o Tune (directly operate on the RLlib Algorithm object)..(not use this one)
    if args.no_tune:
        assert not args.as_test and not args.as_release_test
        algo = config.build()
        for i in range(stop.get(TRAINING_ITERATION, args.stop_iters)):
            results = algo.train()
            if ENV_RUNNER_RESULTS in results:
                mean_return = results[ENV_RUNNER_RESULTS].get(
                    EPISODE_RETURN_MEAN, np.nan
                )
                print(f"iter={i} R={mean_return}", end="")
            if (
                EVALUATION_RESULTS in results
                and ENV_RUNNER_RESULTS in results[EVALUATION_RESULTS]
            ):
                Reval = results[EVALUATION_RESULTS][ENV_RUNNER_RESULTS][
                    EPISODE_RETURN_MEAN
                ]
                print(f" R(eval)={Reval}", end="")
            print()
            for key, threshold in stop.items():
                val = results
                for k in key.split("/"):
                    try:
                        val = val[k]
                    except KeyError:
                        val = None
                        break
                if val is not None and not np.isnan(val) and val >= threshold:
                    print(f"Stop criterium ({key}={threshold}) fulfilled!")
                    if not keep_ray_up:
                        ray.shutdown()
                    return results

        if not keep_ray_up:
            ray.shutdown()
        return results

    # Run the experiment using Ray Tune.

    # Log results using WandB.
    tune_callbacks = tune_callbacks or []
    if hasattr(args, "wandb_key") and (
        args.wandb_key is not None or WANDB_ENV_VAR in os.environ
    ):
        wandb_key = args.wandb_key or os.environ[WANDB_ENV_VAR]
        project = args.wandb_project or (
            args.algo.lower() + "-" + re.sub("\\W+", "-", str(config.env).lower())
        )
        tune_callbacks.append(
            WandbLoggerCallback(
                api_key=wandb_key,
                project=project,
                upload_checkpoints=True,
                **({"name": args.wandb_run_name} if args.wandb_run_name else {}),
            )
        )
    # Auto-configure a CLIReporter (to log the results to the console).
    # Use better ProgressReporter for multi-agent cases: List individual policy rewards.
    if progress_reporter is None and args.num_agents > 0:
        progress_reporter = CLIReporter(
            metric_columns={
                **{
                    TRAINING_ITERATION: "iter",
                    "time_total_s": "total time (s)",
                    NUM_ENV_STEPS_SAMPLED_LIFETIME: "ts",
                    f"{ENV_RUNNER_RESULTS}/{EPISODE_RETURN_MEAN}": "combined return",
                },
                **{
                    (
                        f"{ENV_RUNNER_RESULTS}/module_episode_returns_mean/" f"{pid}"
                    ): f"return {pid}"
                    for pid in config.policies
                },
            },
        )

    # Force Tuner to use old progress output as the new one silently ignores our custom (this is main code for running the example script)
    # `CLIReporter`.
    os.environ["RAY_AIR_NEW_OUTPUT"] = "0"

    # Run the actual experiment (using Tune).
    start_time = time.time()
    results = tune.Tuner(
        trainable or config.algo_class,
        param_space=config,
        run_config=tune.RunConfig(
            stop=stop,
            verbose=args.verbose,
            callbacks=tune_callbacks,
            checkpoint_config=tune.CheckpointConfig(
                checkpoint_frequency=args.checkpoint_freq,
                checkpoint_at_end=args.checkpoint_at_end,
            ),
            progress_reporter=progress_reporter,
        ),
        tune_config=tune.TuneConfig(
            num_samples=args.num_samples,
            max_concurrent_trials=args.max_concurrent_trials,
            scheduler=scheduler,
        ),
    ).fit()
    time_taken = time.time() - start_time

    if not keep_ray_up:
        ray.shutdown()

    # Error out, if Tuner.fit() failed to run. Otherwise, erroneous examples might pass
    # the CI tests w/o us knowing that they are broken (b/c some examples do not have
    # a --as-test flag and/or any passing criteris).
    if results.errors:
        raise RuntimeError(
            "Running the example script resulted in one or more errors! "
            f"{[e.args[0].args[2] for e in results.errors]}"
        )

    # If run as a test, check whether we reached the specified success criteria.
    test_passed = False
    if args.as_test:
        # Success metric not provided, try extracting it from `stop`.
        if success_metric is None:
            for try_it in [
                f"{EVALUATION_RESULTS}/{ENV_RUNNER_RESULTS}/{EPISODE_RETURN_MEAN}",
                f"{ENV_RUNNER_RESULTS}/{EPISODE_RETURN_MEAN}",
            ]:
                if try_it in stop:
                    success_metric = {try_it: stop[try_it]}
                    break
            if success_metric is None:
                success_metric = {
                    f"{ENV_RUNNER_RESULTS}/{EPISODE_RETURN_MEAN}": args.stop_reward,
                }
        # TODO (sven): Make this work for more than one metric (AND-logic?).
        # Get maximum value of `metric` over all trials
        # (check if at least one trial achieved some learning, not just the final one).
        success_metric_key, success_metric_value = next(iter(success_metric.items()))
        best_value = max(
            row[success_metric_key] for _, row in results.get_dataframe().iterrows()
        )
        if best_value >= success_metric_value:
            test_passed = True
            print(f"`{success_metric_key}` of {success_metric_value} reached! ok")

        if args.as_release_test:
            trial = results._experiment_analysis.trials[0]
            stats = trial.last_result
            stats.pop("config", None)
            json_summary = {
                "time_taken": float(time_taken),
                "trial_states": [trial.status],
                "last_update": float(time.time()),
                "stats": stats,
                "passed": [test_passed],
                "not_passed": [not test_passed],
                "failures": {str(trial): 1} if not test_passed else {},
            }
            with open(
                os.environ.get("TEST_OUTPUT_JSON", "/tmp/learning_test.json"),
                "wt",
            ) as f:
                try:
                    json.dump(json_summary, f)
                # Something went wrong writing json. Try again w/ simplified stats.
                except Exception:
                    from ray.rllib.algorithms.algorithm import Algorithm

                    simplified_stats = {
                        k: stats[k] for k in Algorithm._progress_metrics if k in stats
                    }
                    json_summary["stats"] = simplified_stats
                    json.dump(json_summary, f)

        if not test_passed:
            raise ValueError(
                f"`{success_metric_key}` of {success_metric_value} not reached!"
            )

    return results

In [19]:

# 训练
print("开始训练...")
results = run_rllib_example_script_experiment(base_config, args, keep_ray_up=True)
print("训练完成")


开始训练...


2025-07-17 16:39:20,386	INFO worker.py:1723 -- Connecting to existing Ray cluster at address: 192.168.0.25:6379...
2025-07-17 16:39:20,386	INFO worker.py:1747 -- Calling ray.init() again after it has already been called.


== Status ==
Current time: 2025-07-17 16:46:42 (running for 00:00:00.13)
Using FIFO scheduling algorithm.
Logical resource usage: 3.0/24 CPUs, 1.0/1 GPUs (0.0/1.0 accelerator_type:G)
Result logdir: /tmp/ray/session_2025-07-16_19-35-01_925624_3216414/artifacts/2025-07-17_16-46-42/PPO_2025-07-17_16-46-42/driver_artifacts
Number of trials: 1/1 (1 PENDING)


== Status ==
Current time: 2025-07-17 16:46:47 (running for 00:00:05.15)
Using FIFO scheduling algorithm.
Logical resource usage: 3.0/24 CPUs, 1.0/1 GPUs (0.0/1.0 accelerator_type:G)
Result logdir: /tmp/ray/session_2025-07-16_19-35-01_925624_3216414/artifacts/2025-07-17_16-46-42/PPO_2025-07-17_16-46-42/driver_artifacts
Number of trials: 1/1 (1 PENDING)


== Status ==
Current time: 2025-07-17 16:46:52 (running for 00:00:10.24)
Using FIFO scheduling algorithm.
Logical resource usage: 3.0/24 CPUs, 1.0/1 GPUs (0.0/1.0 accelerator_type:G)
Result logdir: /tmp/ray/session_2025-07-16_19-35-01_925624_3216414/artifacts/2025-07-17_16-46-42/PPO_20

2025-07-17 16:46:55,113	WARNING trial.py:863 -- Stopping criterion 'env_runners/episode_return_mean' not found in result dict! Available keys are ['num_training_step_calls_per_iteration', 'num_env_steps_sampled_lifetime', 'done', 'training_iteration', 'trial_id', 'date', 'timestamp', 'time_this_iter_s', 'time_total_s', 'pid', 'hostname', 'node_ip', 'time_since_restore', 'iterations_since_restore', 'timers/training_iteration', 'timers/restore_env_runners', 'timers/training_step', 'timers/env_runner_sampling_timer', 'timers/learner_update_timer', 'timers/synch_weights', 'env_runners/env_step_timer', 'env_runners/sample', 'env_runners/num_env_steps_sampled', 'env_runners/env_to_module_sum_episodes_length_out', 'env_runners/rlmodule_inference_timer', 'env_runners/env_to_module_sum_episodes_length_in', 'env_runners/env_reset_timer', 'env_runners/weights_seq_no', 'env_runners/num_env_steps_sampled_lifetime', 'env_runners/connector_pipeline_timer', 'env_runners/num_env_steps_sampled_lifetime_

2025-07-17 16:46:56,828	WARNING util.py:201 -- The `callbacks.on_trial_result` operation took 1.715 s, which may be a performance bottleneck.
2025-07-17 16:46:56,832	WARNING util.py:201 -- The `process_trial_result` operation took 1.720 s, which may be a performance bottleneck.
2025-07-17 16:46:56,832	WARNING util.py:201 -- Processing trial results took 1.720 s, which may be a performance bottleneck. Please consider reporting results less frequently to Ray Tune.
2025-07-17 16:46:56,832	WARNING util.py:201 -- The `process_trial_result` operation took 1.721 s, which may be a performance bottleneck.


== Status ==
Current time: 2025-07-17 16:46:57 (running for 00:00:15.33)
Using FIFO scheduling algorithm.
Logical resource usage: 3.0/24 CPUs, 1.0/1 GPUs (0.0/1.0 accelerator_type:G)
Result logdir: /tmp/ray/session_2025-07-16_19-35-01_925624_3216414/artifacts/2025-07-17_16-46-42/PPO_2025-07-17_16-46-42/driver_artifacts
Number of trials: 1/1 (1 RUNNING)


== Status ==
Current time: 2025-07-17 16:47:02 (running for 00:00:20.34)
Using FIFO scheduling algorithm.
Logical resource usage: 3.0/24 CPUs, 1.0/1 GPUs (0.0/1.0 accelerator_type:G)
Result logdir: /tmp/ray/session_2025-07-16_19-35-01_925624_3216414/artifacts/2025-07-17_16-46-42/PPO_2025-07-17_16-46-42/driver_artifacts
Number of trials: 1/1 (1 RUNNING)




2025-07-17 16:47:04,275	INFO tune.py:1009 -- Wrote the latest version of all result files and experiment state to '/home/qrbao/ray_results/PPO_2025-07-17_16-46-42' in 0.0939s.


== Status ==
Current time: 2025-07-17 16:47:04 (running for 00:00:21.72)
Using FIFO scheduling algorithm.
Logical resource usage: 3.0/24 CPUs, 1.0/1 GPUs (0.0/1.0 accelerator_type:G)
Result logdir: /tmp/ray/session_2025-07-16_19-35-01_925624_3216414/artifacts/2025-07-17_16-46-42/PPO_2025-07-17_16-46-42/driver_artifacts
Number of trials: 1/1 (1 TERMINATED)
+---------------------+------------+----------------------+--------+------------------+------+-------------------+-----------------+---------------------+---------------------+---------------------+---------------------+-----------------+-----------------+---------------------+-----------------+-----------------+
| Trial name          | status     | loc                  |   iter |   total time (s) |   ts |   combined return |   return prey_3 |   return predator_1 |   return predator_2 |   return predator_4 |   return predator_3 |   return prey_2 |   return prey_0 |   return predator_0 |   return prey_1 |   return prey_4 |
|-----------

2025-07-17 16:47:09,261	INFO tune.py:1041 -- Total run time: 26.72 seconds (21.63 seconds for the tuning loop).


训练完成



###----------------------------------###
# 推理部分
###----------------------------------###        



In [17]:

# 获取最佳结果
print("获取最佳checkpoint...")
best_result = results.get_best_result(
    metric=f"{ENV_RUNNER_RESULTS}/{EPISODE_RETURN_MEAN}", mode="max"
)


获取最佳checkpoint...


In [18]:

print("加载所有智能体的RLModule...")
rl_modules = {}
# 修改：使用新的智能体命名方式
predator_agents = [f"predator_{i}" for i in range(args.n_predators)]
prey_agents = [f"prey_{i}" for i in range(args.n_preys)]
all_agent_names = predator_agents + prey_agents

for agent_name in all_agent_names:
    rl_module_path = os.path.join(
        best_result.checkpoint.path,
        "learner_group",
        "learner",
        "rl_module",
        agent_name,
    )
    
    if os.path.exists(rl_module_path):
        rl_modules[agent_name] = RLModule.from_checkpoint(rl_module_path)
        print(f"成功加载 {agent_name} 的模型")
    else:
        print(f"警告: 找不到 {agent_name} 的模型路径: {rl_module_path}")

print(f"总共加载了 {len(rl_modules)} 个智能体模型")


2025-07-17 16:07:20,361	WARNING deprecation.py:50 -- DeprecationWarning: `RLModule(config=[RLModuleConfig object])` has been deprecated. Use `RLModule(observation_space=.., action_space=.., inference_only=.., model_config=.., catalog_class=..)` instead. This will raise an error in the future!


加载所有智能体的RLModule...
成功加载 predator_0 的模型
成功加载 predator_1 的模型
成功加载 predator_2 的模型
成功加载 predator_3 的模型
成功加载 predator_4 的模型
成功加载 prey_0 的模型
成功加载 prey_1 的模型
成功加载 prey_2 的模型
成功加载 prey_3 的模型
成功加载 prey_4 的模型
总共加载了 10 个智能体模型


In [19]:

# 修复的保存GIF函数
def save_frames_as_gif(frames, filename, duration=100, output_dir="outputs"):
    """将帧序列保存为GIF
    
    Args:
        frames: 帧序列列表
        filename: 文件名（不包含扩展名）
        duration: 每帧持续时间（毫秒）
        output_dir: 输出目录
    """
    if not frames:
        print("没有帧可以保存")
        return None
    
    # 确保输出目录存在
    output_path = Path(output_dir)
    output_path.mkdir(exist_ok=True)
    
    # 生成完整的文件路径
    filepath = output_path / f"{filename}.gif"
    
    # 将numpy数组转换为PIL图像
    pil_frames = []
    for frame in frames:
        if isinstance(frame, np.ndarray):
            # 如果是numpy数组，转换为PIL图像
            if frame.dtype != np.uint8:
                frame = (frame * 255).astype(np.uint8)
            pil_frames.append(Image.fromarray(frame))
        else:
            pil_frames.append(frame)
    
    try:
        # 保存为GIF
        pil_frames[0].save(
            filepath,
            save_all=True,
            append_images=pil_frames[1:],
            duration=duration,
            loop=0
        )
        print(f"GIF已保存到: {filepath.absolute()}")
        return str(filepath.absolute())
    except Exception as e:
        print(f"保存GIF时出错: {e}")
        return None

def get_action_from_rl_module(rl_module, observation, explore=False):
    """从RLModule获取动作"""
    # 将观察转换为torch tensor并添加batch维度
    input_dict = {Columns.OBS: torch.from_numpy(observation).unsqueeze(0)}
    
    if explore:
        # 使用探索性前向传播
        rl_module_out = rl_module.forward_exploration(input_dict)
        action_dist_inputs = rl_module_out["action_dist_inputs"][0]
        action = TorchDiagGaussian.from_logits(action_dist_inputs.unsqueeze(0)).sample().squeeze(0).numpy()
    else:
        # 使用推理前向传播
        rl_module_out = rl_module.forward_inference(input_dict)
        action_dist_inputs = rl_module_out["action_dist_inputs"][0]
        action = TorchDiagGaussian.from_logits(action_dist_inputs.unsqueeze(0)).sample().squeeze(0).numpy()
    
    return action

def get_agent_healths(env, all_agent_names):
    """获取所有智能体的健康值"""
    agent_healths = {}
    try:
        # 尝试从环境中获取健康值
        if hasattr(env, 'env') and hasattr(env.env, 'env') and hasattr(env.env.env, 'env'):
            inner_env = env.env.env.env
            if hasattr(inner_env, 'agents'):
                for i, agent_name in enumerate(all_agent_names):
                    if i < len(inner_env.agents):
                        agent_healths[agent_name] = float(inner_env.agents[i].shape.health)
        else:
            print("无法访问环境的内部结构获取健康值")
    except Exception as e:
        print(f"获取健康值时出错: {e}")
    
    return agent_healths

In [20]:

# 运行推理episodes
print("开始推理...")
for episode in range(args.num_episodes_during_inference):
    print(f"\n=== Episode {episode + 1} ===")
    
    # 创建环境
    env = waterworld_v4.env(
        n_predators=args.n_predators,
        n_preys=args.n_preys,
        agent_algorithms=agent_algos,
        initial_health=100.0,
        render_mode="rgb_array"
    )
    env.reset(seed=42 + episode)
    
    episode_rewards = {agent: 0 for agent in env.agents}
    step_count = 0
    frames = []
    gif_filename = f"waterworld_episode_{episode + 1}"

    try:
        for agent in env.agent_iter():
            observation, reward, termination, truncation, info = env.last()
            
            # 累积奖励
            if agent in episode_rewards:
                episode_rewards[agent] += reward
            
            if termination or truncation:
                action = None
                print(f"{agent} 终止, 奖励: {reward}")
            else:
                # 使用对应的RLModule获取动作
                if agent in rl_modules:
                    try:
                        action = get_action_from_rl_module(
                            rl_modules[agent], 
                            observation, 
                            explore=args.explore_during_inference
                        )
                        # print(f"{agent} 执行动作: {action}")
                    except Exception as e:
                        # print(f"为 {agent} 获取动作时出错: {e}")
                        action = env.action_space(agent).sample()
                        # print(f"{agent} 使用随机动作: {action}")
                else:
                    action = env.action_space(agent).sample()
                    # print(f"{agent} 没有找到对应模型，使用随机动作: {action}")
            
            env.step(action)
            step_count += 1
            
            # 每隔几步捕获一帧
            if step_count % 10 == 0:
                try:
                    frame = env.render()
                    if frame is not None:
                        frames.append(frame)
                except Exception as e:
                    print(f"渲染第{step_count}步时出错: {e}")

            # 每100步输出一次进度
            if step_count % 100 == 0:
                print(f"已执行 {step_count} 步")
                
    except KeyboardInterrupt:
        print("用户中断")
        break
    except Exception as e:
        print(f"Episode {episode + 1} 出现错误: {e}")
    finally:
        # 获取最终的健康值
        final_healths = get_agent_healths(env, all_agent_names)
        env.close()
    
    # 保存GIF并记录到wandb
    gif_path = None
    if frames:
        gif_path = save_frames_as_gif(frames, gif_filename, duration=100, output_dir="outputs")
    
    # 准备日志数据
    log_data = {
        "episode_index": episode,
        "total_reward_mean": np.mean(list(episode_rewards.values())),
        "total_reward_std": np.std(list(episode_rewards.values())),
        "episode_steps": step_count,
    }
    
    # 添加每个智能体的奖励
    for agent_name, reward in episode_rewards.items():
        log_data[f"reward/{agent_name}"] = reward
    
    # 添加健康值信息
    if final_healths:
        for agent_name, health in final_healths.items():
            log_data[f"health/{agent_name}"] = health
        
        health_values = list(final_healths.values())
        log_data["health/mean"] = np.mean(health_values)
        log_data["health/std"] = np.std(health_values)
        log_data["health/min"] = np.min(health_values)
        log_data["health/max"] = np.max(health_values)
    
    # 添加GIF到wandb
    if gif_path and Path(gif_path).exists():
        try:
            log_data["episode_gif"] = wandb.Video(gif_path, fps=10, format="gif")
            print(f"成功添加GIF到wandb: {gif_path}")
        except Exception as e:
            print(f"添加GIF到wandb时出错: {e}")
    
    # 记录到wandb
    try:
        wandb.log(log_data)
        print(f"成功记录episode {episode + 1}的数据到wandb")
    except Exception as e:
        print(f"记录到wandb时出错: {e}")
    
    # 输出episode结果
    print(f"Episode {episode + 1} 完成")
    print("各智能体总奖励:")
    for agent, total_reward in episode_rewards.items():
        print(f"  {agent}: {total_reward:.2f}")
    print(f"总步数: {step_count}")
    
    if final_healths:
        print("各智能体最终健康值:")
        for agent, health in final_healths.items():
            print(f"  {agent}: {health:.2f}")

开始推理...

=== Episode 1 ===
Reset complete:
  Agents: ['predator_0', 'predator_1', 'predator_2', 'predator_3', 'predator_4', 'prey_0', 'prey_1', 'prey_2', 'prey_3', 'prey_4']
  _cumulative_rewards keys: ['predator_0', 'predator_1', 'predator_2', 'predator_3', 'predator_4', 'prey_0', 'prey_1', 'prey_2', 'prey_3', 'prey_4']
[WARNING]: Received an action [ 1.0808817 -3.227683 ] that was outside action space Box(-1.0, 1.0, (2,), float32). Environment is clipping to space
[WARNING]: Received an action [0.08019881 1.9862385 ] that was outside action space Box(-1.0, 1.0, (2,), float32). Environment is clipping to space
[WARNING]: Received an action [-0.21774466 -1.3638964 ] that was outside action space Box(-1.0, 1.0, (2,), float32). Environment is clipping to space
[WARNING]: Received an action [-0.47705397  1.0888759 ] that was outside action space Box(-1.0, 1.0, (2,), float32). Environment is clipping to space
[WARNING]: Received an action [1.0670633  0.09879686] that was outside action spa

wandb: WARNING `fps` argument does not affect the frame rate of the video when providing a file path or raw bytes.


GIF已保存到: /home/qrbao/Documents/code4/rllib/mycode2_algorithm/outputs/waterworld_episode_1.gif
成功添加GIF到wandb: /home/qrbao/Documents/code4/rllib/mycode2_algorithm/outputs/waterworld_episode_1.gif
成功记录episode 1的数据到wandb
Episode 1 完成
各智能体总奖励:
  predator_0: -103.09
  predator_1: -112.62
  predator_2: -96.68
  predator_3: -91.61
  predator_4: -99.85
  prey_0: -58.01
  prey_1: -29.03
  prey_2: -110.07
  prey_3: -88.90
  prey_4: -219.77
总步数: 4637
各智能体最终健康值:
  predator_0: 110.00
  predator_1: 100.00
  predator_2: 112.00
  predator_3: 112.00
  predator_4: 100.00
  prey_0: 139.02
  prey_1: 0.00
  prey_2: 99.00
  prey_3: 121.01
  prey_4: 99.00

=== Episode 2 ===
Reset complete:
  Agents: ['predator_0', 'predator_1', 'predator_2', 'predator_3', 'predator_4', 'prey_0', 'prey_1', 'prey_2', 'prey_3', 'prey_4']
  _cumulative_rewards keys: ['predator_0', 'predator_1', 'predator_2', 'predator_3', 'predator_4', 'prey_0', 'prey_1', 'prey_2', 'prey_3', 'prey_4']
[WARNING]: Received an action [-0.47747952 -2

wandb: WARNING `fps` argument does not affect the frame rate of the video when providing a file path or raw bytes.


GIF已保存到: /home/qrbao/Documents/code4/rllib/mycode2_algorithm/outputs/waterworld_episode_2.gif
成功添加GIF到wandb: /home/qrbao/Documents/code4/rllib/mycode2_algorithm/outputs/waterworld_episode_2.gif
成功记录episode 2的数据到wandb
Episode 2 完成
各智能体总奖励:
  predator_0: -106.50
  predator_1: -101.31
  predator_2: -105.97
  predator_3: -112.44
  predator_4: -100.31
  prey_0: -101.36
  prey_1: -74.55
  prey_2: -91.39
  prey_3: -90.70
  prey_4: -197.89
总步数: 5010
各智能体最终健康值:
  predator_0: 106.00
  predator_1: 106.00
  predator_2: 100.00
  predator_3: 100.00
  predator_4: 100.00
  prey_0: 100.00
  prey_1: 138.03
  prey_2: 120.01
  prey_3: 118.01
  prey_4: 119.01

=== Episode 3 ===
Reset complete:
  Agents: ['predator_0', 'predator_1', 'predator_2', 'predator_3', 'predator_4', 'prey_0', 'prey_1', 'prey_2', 'prey_3', 'prey_4']
  _cumulative_rewards keys: ['predator_0', 'predator_1', 'predator_2', 'predator_3', 'predator_4', 'prey_0', 'prey_1', 'prey_2', 'prey_3', 'prey_4']
[WARNING]: Received an action [-0.4618

...

GIF已保存到: /home/qrbao/Documents/code4/rllib/mycode2_algorithm/outputs/waterworld_episode_8.gif
成功添加GIF到wandb: /home/qrbao/Documents/code4/rllib/mycode2_algorithm/outputs/waterworld_episode_8.gif
成功记录episode 8的数据到wandb
Episode 8 完成
各智能体总奖励:
  predator_0: -111.04
  predator_1: -112.94
  predator_2: -105.36
  predator_3: -100.02
  predator_4: -99.57
  prey_0: -84.96
  prey_1: -75.30
  prey_2: -113.80
  prey_3: -98.40
  prey_4: -219.63
总步数: 5010
各智能体最终健康值:
  predator_0: 100.00
  predator_1: 100.00
  predator_2: 103.00
  predator_3: 103.00
  predator_4: 100.00
  prey_0: 119.03
  prey_1: 139.02
  prey_2: 99.00
  prey_3: 114.01
  prey_4: 98.00

=== Episode 9 ===
Reset complete:
  Agents: ['predator_0', 'predator_1', 'predator_2', 'predator_3', 'predator_4', 'prey_0', 'prey_1', 'prey_2', 'prey_3', 'prey_4']
  _cumulative_rewards keys: ['predator_0', 'predator_1', 'predator_2', 'predator_3', 'predator_4', 'prey_0', 'prey_1', 'prey_2', 'prey_3', 'prey_4']
[WARNING]: Received an action [-0.3548553

wandb: WARNING `fps` argument does not affect the frame rate of the video when providing a file path or raw bytes.


GIF已保存到: /home/qrbao/Documents/code4/rllib/mycode2_algorithm/outputs/waterworld_episode_9.gif
成功添加GIF到wandb: /home/qrbao/Documents/code4/rllib/mycode2_algorithm/outputs/waterworld_episode_9.gif
成功记录episode 9的数据到wandb
Episode 9 完成
各智能体总奖励:
  predator_0: -103.79
  predator_1: -112.97
  predator_2: -94.45
  predator_3: -90.26
  predator_4: -100.80
  prey_0: -68.99
  prey_1: -115.42
  prey_2: -32.62
  prey_3: -9.75
  prey_4: -203.39
总步数: 4558
各智能体最终健康值:
  predator_0: 110.00
  predator_1: 100.00
  predator_2: 112.00
  predator_3: 112.00
  predator_4: 100.00
  prey_0: 136.02
  prey_1: 97.00
  prey_2: 178.04
  prey_3: 0.00
  prey_4: 118.01

=== Episode 10 ===
Reset complete:
  Agents: ['predator_0', 'predator_1', 'predator_2', 'predator_3', 'predator_4', 'prey_0', 'prey_1', 'prey_2', 'prey_3', 'prey_4']
  _cumulative_rewards keys: ['predator_0', 'predator_1', 'predator_2', 'predator_3', 'predator_4', 'prey_0', 'prey_1', 'prey_2', 'prey_3', 'prey_4']
[WARNING]: Received an action [0.14337239 1

wandb: WARNING `fps` argument does not affect the frame rate of the video when providing a file path or raw bytes.


GIF已保存到: /home/qrbao/Documents/code4/rllib/mycode2_algorithm/outputs/waterworld_episode_10.gif
成功添加GIF到wandb: /home/qrbao/Documents/code4/rllib/mycode2_algorithm/outputs/waterworld_episode_10.gif
成功记录episode 10的数据到wandb
Episode 10 完成
各智能体总奖励:
  predator_0: -104.16
  predator_1: -112.84
  predator_2: -108.34
  predator_3: -102.71
  predator_4: -103.11
  prey_0: -84.70
  prey_1: -45.74
  prey_2: -111.48
  prey_3: -54.70
  prey_4: -218.13
总步数: 4705
各智能体最终健康值:
  predator_0: 110.00
  predator_1: 100.00
  predator_2: 100.00
  predator_3: 100.00
  predator_4: 100.00
  prey_0: 119.01
  prey_1: 0.00
  prey_2: 99.00
  prey_3: 157.03
  prey_4: 98.00


In [21]:
print("推理完成!")
wandb.finish()

推理完成!
